In [ ]:
from netgen.occ import *
from ngsolve import *
from ngsolve.webgui import Draw

square = Rectangle(1,1).Face()
circ = Circle ( (0.4, 0.3), 0.2).Face()
circ.edges.name = "interface"
outer = square-circ

circ.faces.name = "conductor"
outer.faces.name = "air"
square.edges.Max(Y).name = "top"
square.edges.Min(Y).name = "bot"

shape = Glue([outer,circ])
mesh = Mesh(OCCGeometry(shape, dim=2).GenerateMesh(maxh=0.05)).Curve(3)
Draw (mesh);

### Version 1: use very high conductivity in conductor

In [ ]:
fes = H1(mesh, order=3, dirichlet="bot|top")
u,v = fes.TnT()

lam = mesh.MaterialCF( { "conductor" : 1e8}, 1)
bfa = BilinearForm (lam*grad(u)*grad(v)*dx).Assemble()

gfu = GridFunction(fes)
gfu.Set(1, definedon=mesh.Boundaries("top"))

gfu.vec.data -= bfa.mat.Inverse(freedofs=fes.FreeDofs()) @ bfa.mat * gfu.vec
Draw (gfu);

### Version 2: global basis function as GridFunction

In [ ]:
fes = H1(mesh, order=1, dirichlet="bot|top")
gfbasis = GridFunction(fes)
gfbasis.Set(1, definedon=mesh.Materials("conductor"))
Draw (gfbasis);

In [ ]:
fes1 = H1(mesh, order=3, definedon="air", dirichlet="interface|bot|top")
fes2 = NumberSpace(mesh)
X = fes1*fes2

(u,u0), (v,v0) = X.TnT()

bfa = BilinearForm( (grad(u)+u0*grad(gfbasis)) * (grad(v)+v0*grad(gfbasis)) * dx).Assemble()
gfu = GridFunction(X)

gfu.components[0].Set(1, definedon=mesh.Boundaries("top"))
gfu.vec.data -= bfa.mat.Inverse(freedofs=X.FreeDofs()) @ bfa.mat * gfu.vec
Draw (gfu.components[0]+gfu.components[1]*gfbasis, mesh);